# Codigo Final Algoritmo Evolutivo - Aplicar a Base de datos Total - Reestricciones Variables especificas(Rangos) y Variables Fijas

## 1. Cargamos el Algoritmo Genetico

In [172]:
## 1. Parte 1, 

import pandas as pd
from io import BytesIO
import json

from random import Random
from time import time
from inspyred import ec
from random import Random
from time import time
import numpy as np
import tensorflow as tf
import time
 
from minio import Minio  # Cliente de Python para interactuar con el servidor MinIO.
import urllib3   # Biblioteca para realizar peticiones HTTP


# Parte 4, Algoritmo Genetico

#### Parametros a modificar en el Algoritmo Genetico,
#### window_size y   (individuo_reshape = np.array(candidate).reshape(1, 1, 14), donde modificas, (1,n_pasos_LSTM, n_variables)
#############################################################################################################################################

# # 1. Cargar el modelo LSTM guardado
modelo_lstm = tf.keras.models.load_model('modelo_lstm_14var_vf3.h5')

# 2. Leer el archivo Parquet en un DataFrame de pandas
# df = pd.read_parquet('train_lstm_tail_50.parquet', engine='pyarrow')
# datos_genetic = df.head(4)
# datos_genetic = pd.read_parquet('train_lstm_tail_50.parquet', engine='pyarrow')

# 3. Definir el Tamaño de la ventana (Depende con cuantos pasos atras entrenaste la LSTM, 1: solo usa 1 fila, 2: solo usa 2 filas, etc)
##### PARAMETRO A MODIFICAR
##########################################################################################################################################

window_size = 1   

# # Lista para almacenar los subconjuntos de datos que iran entregando al Algoritmo Evolutivo
# resultados = []
# # Recorrer el DataFrame usando ventanas deslizantes
# for start in range(len(bloques_origen_b1_escalado)):  # Ingresa Bloque por bloque
#     # Crear un subconjunto del DataFrame
#     subset = bloques_origen_b1_escalado.iloc[start:start + window_size].copy()
    
#     # Si el subconjunto tiene menos filas que el tamaño de la ventana, agregar filas con NaN
#     if len(subset) < window_size:
#         filas_faltantes = window_size - len(subset)
#         filas_nan = pd.DataFrame(np.nan, index=range(filas_faltantes), columns=bloques_origen_b1_escalado.columns)
#         subset = pd.concat([subset, filas_nan], ignore_index=True)
    
#     resultados.append(subset)


# Función para particionar el DataFrame
def create_sliding_windows(df, window_size):
    """
    Divide el DataFrame en ventanas deslizantes.
    
    Args:
    df (pd.DataFrame): DataFrame original.
    window_size (int): Tamaño de la ventana.
    
    Returns:
    list: Lista de DataFrames (ventanas).
    """
    windows = []
    for start in range(len(df)):
        subset = df.iloc[start:start + window_size].copy()
        
        # Rellenar con NaN si la ventana es menor al tamaño deseado
        if len(subset) < window_size:
            filas_faltantes = window_size - len(subset)
            filas_nan = pd.DataFrame(np.nan, index=range(filas_faltantes), columns=df.columns)
            subset = pd.concat([subset, filas_nan], ignore_index=True)
        
        windows.append(subset)
    return windows

###############################################################################################################################################

config_2 = {
    "dynamic_limits": {
        "roll": "fixed",  
        "intake manifold pressure": (-0.0005, 0.0005), 
        "intake manifold #2 pressure": (-0.0005, 0.0005),  
        "engine speed": (-0.209, 0.209), 
        "actual gear": (-0.3, 0.3),    
        "x": "fixed", 
        "y": "fixed",    
        "z": "fixed", 
        "efhcargado": "fixed",  
        "efhvacio": "fixed", 
        "distancia_ruta_pendiente_grados": "fixed",    
        "ambient air temperature": "fixed", 
        "brake pump pressure": (-0.0766, 0),    
        "fuel consumption rate(lag1)": "fixed"    
    }
}

def generate_dynamic_limits(row, config):
    """
    Genera X_min y X_max para una fila específica basada en configuraciones personalizadas.
    
    Parameters:
    row (array-like): Fila del DataFrame.
    config (dict): Configuración de límites dinámicos por columna.
    
    Returns:
    X_min, X_max (arrays): Arrays con los límites mínimos y máximos.
    """
    #Estas listas se llenarán con los límites mínimos (X_min) y máximos (X_max) para cada valor en la fila procesada
    X_min = []
    X_max = []
    
    for i, value in enumerate(row): # enumerate, nos permite iterar sobre los valores de la fila (row) y obtener tanto el índice i como el valor value
        variable_name = config["column_names"][i]  # config["column_names"] contiene los nombres de las columnas en el orden en que aparecen en el DataFrame.
        
        # Si el nombre de la columna tiene la etiqueta "fixed" en config["dynamic_limits"], la variable es fija y no debe modificarse
        if config["dynamic_limits"].get(variable_name) == "fixed":  # 
            # Variable fija, los límites son el mismo valor
            X_min.append(value)
            X_max.append(value)
        else:
            # Aplicar los límites dinámicos definidos
            lower, upper = config["dynamic_limits"][variable_name]

            # Si value = 0.1 y lower = -0.2: value+lower=0.1−0.2=−0.1, new_min=max⁡(0,−0.1)=0, y asi Evitamos negativos en valores escalados 
            new_min = max(0, value + lower)  #  # Evitar negativos en valores escalados , en este caso minimo es 0, porque es max-minescaler, en otro escalador puede ser -1

            # Si value = 0.8 y upper = 0.3: value+upper=0.8+0.3=1.1, new_max=min⁡(1,1.1)=1, y asi evitamos valores por encima de 1 en valores escalados
            new_max = min(1, value + upper)  # Limitar al rango [0, 1] escalado, en este caso minimo es 1, porque es max-minescaler, en otro escalador puede ser 1, etc

            
            # Obtiene los valores lower (límite inferior) y upper (límite superior) definidos en el diccionario de configuración para la columna actual (variable_name).
            # lower, upper = config["dynamic_limits"][variable_name]
            # new_min = max(0, value + lower)  # Evitar valores negativos
            # new_max = max(new_min, value + upper)  # Asegurar que X_max >= X_min
            
            # X_min.append(value + lower)
            # X_max.append(value + upper)
            X_min.append(new_min)
            X_max.append(new_max)
    
    return np.array(X_min), np.array(X_max)


def generate_individual(random, df, start_index, n_var_independientes, ventana, config):
    """
    Genera un individuo basado en configuraciones personalizadas.
    asegurándose de que no se generen valores negativos.
    
    Parameters:
    random (Random): Generador aleatorio.
    df (DataFrame): DataFrame con los datos originales.
    start_index (int): Índice de inicio para seleccionar las filas consecutivas.
    n_var_independientes (int): Número de variables independientes a considerar (columnas).
    ventana (int): Tamaño de la ventana (número de filas a seleccionar).
    config (dict): Configuración personalizada para los límites dinámicos.
    
    Returns:
    individual (array): Array de tamaño `(ventana, n_var_independientes)` con los valores generados.
    """
    individual = []

    # Asegurarse de trabajar solo con las primeras `n_var_independientes` columnas(No debemos incluir la columna Target: En este caso la ultima columna)
    df_independientes = df.iloc[:, :n_var_independientes]  # Selecciona únicamente las primeras n_var_independientes columnas del DataFrame 
    config["column_names"] = df_independientes.columns.tolist() # Guarda los nombres de estas columnas en config["column_names"] para usarlos más adelante en la generación de límites dinámicos.

    # Verificar que el índice de inicio + ventana no exceda el número de filas en df_independientes
    if start_index + ventana > len(df_independientes):
        raise IndexError(f"El índice de inicio más la ventana excede el número de filas disponibles en el DataFrame (inicio: {start_index}, ventana: {ventana}).")
    
    # Iterar a través de la ventana
    for i in range(ventana): # Itera sobre las filas consecutivas del DataFrame, comenzando desde start_index
        row = df_independientes.iloc[start_index + i].values
        
        # Generar límites dinámicos para la fila actual
        X_min, X_max = generate_dynamic_limits(row, config = config)

        # Generar una fila del individuo respetando los límites
        # random_row = [random.uniform(X_min[j], X_max[j]) for j in range(len(row))]

        # Generar una fila del individuo respetando los límites
        random_row = []
        for j in range(len(row)):
            value = random.uniform(X_min[j], X_max[j])  # Generar valor dentro de los límites
            if value < 0:  # Si el valor es negativo, conservar el original del individuo original del df, como ya hemos limitado en
                # generate_dynamic_limits() con new_min = max(0, value + lower), esta linea podria ser omitida, pero conservemosla
                value = row[j]
            random_row.append(value)
        
        # Añadir la fila generada al individuo
        individual.append(random_row)
    
    return np.array(individual)


# import random
# window_size = 1
# individuo = generate_individual(random, resultados[10], start_index=0, n_var_independientes=14, ventana=window_size, config = config_2)
# individuo

def fitness_function(candidates, args, modelo_lstm):
    fitness_values = []
    for candidate in candidates:
        # Ajustar la forma del individuo para que sea compatible con la entrada del modelo LSTM
        individuo_reshape = np.array(candidate).reshape(1, 1, 14)  #  (1, n_pasos_lstm, n_variables) , n_pasos_lstm >> PARAMETRO A MODIFICAR
        
        # Realizar la predicción usando el modelo LSTM
        prediccion = modelo_lstm.predict(individuo_reshape)
        
        # Extraer el valor de la predicción (consumo de combustible) y añadirlo a la lista de fitness
        fitness_values.append(prediccion[0][0])  # Asegúrate de que `prediccion` tenga la forma correcta
    return fitness_values

# # Generar la población inicial
# poblacion = generate_population(n_individuos_poblacion=3, random=random, df=datos_genetic, start_index=0, n_var_independientes=14)

# # # Evaluar la función de fitness en la población generada
# fitness_scores = fitness_function(candidates=poblacion, args=None, modelo_lstm=modelo_lstm)
# print(f"Fitness scores: {fitness_scores}")\

# Función de evaluación y algoritmo genético
# window_size, Tamaño de la ventana (Depende con cuantos pasos atras entrenaste la LSTM, 1: solo usa 1 fila, 2: solo usa 2 filas, etc)

def run_genetic_algorithm(modelo_lstm, df, n_individuos_poblacion=5, generations=5, start_index=0, window_size=1): ##### window_size , PARAMETRO A MODIFICAR
    # Crear el generador de números aleatorios
    prng = Random()
    
    # Número de variables independientes en cada individuo
    n_var_independientes = 14  
    
    # Crear el objeto del algoritmo genético (GA)
    ea = ec.GA(prng)

    # Configurar la función generadora de individuos
    def generator(random, args):
        #return generate_individual(prng, df, start_index, n_var_independientes, window_size)
        #return generate_individual(random, df, start_index=0, n_var_independientes=14, ventana=window_size)
        return generate_individual(random, df, start_index=0, n_var_independientes=14, ventana=window_size, config = config_2)
    
    # Crear un contenedor global para almacenar los fitness de cada generación
    fitness_history = {}

###################################################################################################################################################
    # # Configurar la función de evaluación (fitness)
    # def evaluator(candidates, args):
    #     # Evaluar el fitness de todos los candidatos (individuos)
    #     fitness_values = fitness_function(candidates, args, modelo_lstm)
        
    #     # Obtener el número de generación actual
    #     current_generation = len(fitness_history)
    #     #print(f"Evaluando Generación {current_generation}...")
        
    #     # Guardar los fitness de la generación actual
    #     fitness_history[current_generation] = fitness_values
        
    #     # Mostrar los fitness de la generación actual
    #     #print(f"\nFitness de la Generación {current_generation}: {fitness_values}")
        
    #     return fitness_values

#########################################################################################################################################################
    # Límite de estancamiento
    stagnation_limit = 10
    stagnation_counter = 0
    last_best_fitness = None
    
    # Configurar la función de evaluación (fitness)
    def evaluator(candidates, args):
        nonlocal stagnation_counter, last_best_fitness
    
        # Evaluar el fitness de todos los candidatos (individuos)
        fitness_values = fitness_function(candidates, args, modelo_lstm)
        
        # Obtener el número de generación actual
        current_generation = len(fitness_history)
        
        # Guardar los fitness de la generación actual
        fitness_history[current_generation] = fitness_values
    
        # Calcular el mejor fitness de la generación actual
        current_best_fitness = min(fitness_values)  # Asumes que estás minimizando
        
        # Verificar estancamiento
        if last_best_fitness is not None and current_best_fitness == last_best_fitness:
            stagnation_counter += 1
        else:
            stagnation_counter = 0
    
        # Detener si se alcanza el límite de estancamiento
        if stagnation_counter >= stagnation_limit:
            print(f"Estancamiento detectado en la Generación {current_generation}. Mejor fitness: {current_best_fitness}")
            raise StopIteration("El algoritmo se detuvo debido a estancamiento.")
    
        # Actualizar el último mejor fitness
        last_best_fitness = current_best_fitness
    
        # Mostrar los fitness de la generación actual
        # print(f"Generación {current_generation} - Mejor fitness: {current_best_fitness}")
    
        return fitness_values

#########################################################################################################################################################
    

    # Configuración de operadores genéticos
    ea.variator = [
        ec.variators.uniform_crossover #,  # Cruce uniforme
        #ec.variators.gaussian_mutation   # Mutación gaussiana,  En este caso, no estoy usando Mutacion
    ]

    #ea.variator = [ec.variators.uniform_crossover, custom_mutation]  # Usar custom_mutation

    # Cambiar el método de reemplazo a generational_replacement
    ea.replacer = ec.replacers.generational_replacement
    ea.selector = ec.selectors.tournament_selection  # Selección por torneo

    # Configurar la terminación por número de generaciones
    ea.terminator = ec.terminators.generation_termination
        
    # Ejecutar la evolución
    final_pop = ea.evolve(
        generator=generator,
        evaluator=evaluator,
        pop_size=n_individuos_poblacion,
        maximize=False, #Problema de Minimizacion 
        num_elites=1,
        max_generations=generations
    )

    # Obtener el mejor individuo
    best_individual = min(final_pop, key=lambda x: x.fitness)
    best_fitness = best_individual.fitness

    print("\nMejor individuo (minimizar consumo de combustible):", best_individual.candidate)
    print("Consumo de combustible predicho (fitness):", best_fitness)

    return best_individual.candidate, best_fitness


#Función para aplicar el algoritmo genético por bloques
#window_size, Tamaño de la ventana (Depende con cuantos pasos atras entrenaste la LSTM, 1: solo usa 1 fila, 2: solo usa 2 filas, etc)
def aplicar_algoritmo_genetico_por_bloques(modelo_lstm, resultados, window_size=1, n_individuos_poblacion=5, generations=5): ##### window_size , PARAMETRO A MODIFICAR
    # Nombres de columnas originales del DataFrame
    columnas_originales = resultados[0].columns.tolist()  # Aseguramos que incluya todas las columnas de resultados[0]
    
    # Crear un DataFrame vacío para almacenar los resultados
    df_resultados_final = pd.DataFrame(columns=columnas_originales) 
    
    # Iterar sobre los bloques en resultados con una ventana deslizante
    for i in range(len(resultados) - window_size + 1):  # Ajustamos el rango para no exceder el tamaño del DataFrame
        # Ejecutar el algoritmo genético en el bloque actual, pasando el índice de inicio como `start_index`
        best_individual, best_fitness = run_genetic_algorithm(
            modelo_lstm, resultados[i], n_individuos_poblacion=n_individuos_poblacion, generations=generations, start_index=i, window_size=window_size)
        
        # Extraer solo la última fila de best_individual (la última fila de la matriz 4x14)
        ultima_fila = best_individual[-1]  # Esto obtiene la última fila del array
        
        # Crear una nueva fila con los valores de ultima_fila y best_fitness
        nueva_fila = list(ultima_fila)  # Convertimos la última fila en una lista
        nueva_fila.append(best_fitness)  # Agregamos el best_fitness al final
        
        # Convertimos la fila en un DataFrame temporal
        df_temp = pd.DataFrame([nueva_fila], columns=columnas_originales) 
        
        # Anexamos la fila al DataFrame final
        df_resultados_final = pd.concat([df_resultados_final, df_temp], ignore_index=True)

        # Ajustar el índice del DataFrame final para que comience en window_size - 1
        df_resultados_final.index = range(window_size - 1, window_size - 1 + len(df_resultados_final))

    return df_resultados_final

In [173]:
# resultados = create_sliding_windows(bloques_origen_b1_escalado, window_size)

#########################################################################################################################################################################

# # Medir el tiempo de ejecución del algoritmo genético
# start_time = time.time()

# # resultados -> lista de DataFrames que contiene tus bloques de datos
# # Cambiar el nombre, df_resultados_recomendacion
# # modelo_lstm -> tu modelo LSTM ya entrenado
# #df_resultados_recomendacion_b1 = aplicar_algoritmo_genetico_por_bloques(modelo_lstm, resultados, window_size=1, n_individuos_poblacion=5, generations=5)
# df_resultados_recomendacion_b1 = aplicar_algoritmo_genetico_por_bloques(modelo_lstm, resultados, window_size=1, n_individuos_poblacion=5, generations=5)


# end_time = time.time()

# # Calcular y mostrar el tiempo de ejecución
# elapsed_time = end_time - start_time
# print(f"Tiempo de ejecución del algoritmo genético: {elapsed_time:.2f} segundos")

## 2. Cargamos los Equipos(Camiones) que debemos procesar

In [152]:
from conection_storage import AzureBlobStorage
import pandas as pd

# Definir las columnas necesarias
columnas_necesarias = [
    'roll',
    'intake manifold pressure',
    'intake manifold #2 pressure',
    'engine speed',
    'actual gear',
    'x',
    'y',
    'z',
    'efhcargado',
    'efhvacio',
    'distancia_ruta_pendiente_grados',
    'ambient air temperature',
    'brake pump pressure',
    'fuel consumption rate(lag1)', 
    'fuel consumption rate(target)'
]

# Configuración de la conexión a Azure Blob Storage
config_storage = {
    'accountname': 'datalakemlopsd4m',
    'accountkey': 'iWT8t74/#XlqcqoR03keDVtFZPzr0PB9zDffMPaLWMUBIAjUww8uYAVkc9xRkcBtvTmUHKBvd1sB3+ASt6mGgcQ==',
}

# Conectar al servidor de AzureStorage
storage = AzureBlobStorage(**config_storage)

# Definir las rutas de los archivos Parquet
files_to_process = [
    {
        'container': 'presentation',
        'folder': 'proyectocombustible_presentation/ModeloDinamico/datacamion/28/',
        'filename': '20241202001849_Caso_1.parquet'
    },
    {
        'container': 'presentation',
        'folder': 'proyectocombustible_presentation/ModeloDinamico/datacamion/29/',
        'filename': '20241202001849_Caso_1.parquet'
    },

    {
        'container': 'presentation',
        'folder': 'proyectocombustible_presentation/ModeloDinamico/datacamion/44/',
        'filename': '20241202001849_Caso_1.parquet'
    },

    {
        'container': 'presentation',
        'folder': 'proyectocombustible_presentation/ModeloDinamico/datacamion/45/',
        'filename': '20241202001849_Caso_1.parquet'
    },
    
    # Agrega más archivos según sea necesario
]

# Diccionario para almacenar cada DataFrame por archivo
dataframes_dict = {}

# Leer cada archivo Parquet y guardarlo en el diccionario
for idx, file_info in enumerate(files_to_process, start=1):
    container_name = file_info['container']
    full_path = file_info['folder'] + file_info['filename']
    print(f"Leyendo archivo: {full_path}")
    
    # Leer el archivo desde Azure Storage
    df = storage.read_file(container_name, full_path, 'parquet')
    
    # Ordenar por la columna 'instant_date_t'
    df_sorted = df.sort_values('instant_date_t', ignore_index=True)

    # Filtrar columnas necesarias
    df_sorted = df_sorted[columnas_necesarias]
    
    # Guardar en el diccionario usando el índice o nombre del archivo
    key = f"df_{file_info['folder']}"  #f"df_{idx}"  # O usa file_info['filename'] si prefieres nombres descriptivos
    dataframes_dict[key] = df_sorted   # organiza y almacena cada DataFrame ordenado para su posterior procesamiento. 

# Reemplazar los valores NaN por 0 en cada DataFrame del diccionario
for key, df in dataframes_dict.items():
    print(f"Reemplazando NaN por 0 en el DataFrame: {key}")
    
    # Reemplazar los valores NaN por 0
    df_filled = df.fillna(0)
    
    # Guardar el DataFrame con los valores NaN reemplazados
    dataframes_dict[key] = df_filled

    # Verificar el resultado
    print(f"DataFrame después de reemplazar NaN por 0 en {key}:")
    #print(df_filled.head())  # Mostrar las primeras filas para verificar

Leyendo archivo: proyectocombustible_presentation/ModeloDinamico/datacamion/28/20241202001849_Caso_1.parquet
Leyendo archivo: proyectocombustible_presentation/ModeloDinamico/datacamion/29/20241202001849_Caso_1.parquet
Leyendo archivo: proyectocombustible_presentation/ModeloDinamico/datacamion/44/20241202001849_Caso_1.parquet
Leyendo archivo: proyectocombustible_presentation/ModeloDinamico/datacamion/45/20241202001849_Caso_1.parquet
Reemplazando NaN por 0 en el DataFrame: df_proyectocombustible_presentation/ModeloDinamico/datacamion/28/
DataFrame después de reemplazar NaN por 0 en df_proyectocombustible_presentation/ModeloDinamico/datacamion/28/:
Reemplazando NaN por 0 en el DataFrame: df_proyectocombustible_presentation/ModeloDinamico/datacamion/29/
DataFrame después de reemplazar NaN por 0 en df_proyectocombustible_presentation/ModeloDinamico/datacamion/29/:
Reemplazando NaN por 0 en el DataFrame: df_proyectocombustible_presentation/ModeloDinamico/datacamion/44/
DataFrame después de r

In [166]:
# len(dataframes_dict['df_proyectocombustible_presentation/ModeloDinamico/datacamion/28/'])

In [128]:
def dividir_en_bloques(df, num_bloques=8):
    """
    Divide un DataFrame en bloques del mismo tamaño.
    Args:
        df (pd.DataFrame): DataFrame a dividir.
        num_bloques (int): Número de bloques a crear.
    Returns:
        dict: Diccionario con bloques numerados como claves.
    """
    bloque_sizes = [len(df) // num_bloques + (1 if x < len(df) % num_bloques else 0) for x in range(num_bloques)]
    bloques = {}
    start_idx = 0

    for i, size in enumerate(bloque_sizes):
        end_idx = start_idx + size
        bloques[f'bloque_{i + 1}'] = df.iloc[start_idx:end_idx]
        start_idx = end_idx

    return bloques

In [174]:
# # Variables a normalizar (excluyendo la última columna)
# variables_a_normalizar = bloques_origen['bloque_1'].columns[:-2]  ##  Queda fijo 

# # Excluir el target y el lag, que no se deben escalar
# with open("minimos_lstm_13_var.json", "r") as file:
#     minimos = json.load(file)

# with open("maximos_lstm_13_var.json", "r") as file:
#     maximos = json.load(file)

def normalizar_por_variables_max_min(dataframe, variables_a_normalizar, minimos, maximos):
    """
    Normaliza solo las variables especificadas en un dataframe usando el método Min-Max.
    Args:
        dataframe: El dataframe que se va a normalizar.
        variables_a_normalizar: Lista de nombres de las variables a normalizar.
        minimos: Diccionario con el valor mínimo de cada variable.
        maximos: Diccionario con el valor máximo de cada variable.
    Returns:
        DataFrame normalizado.
    """
    dataframe_normalizado = dataframe.copy()
    for columna in variables_a_normalizar:
        if columna in minimos and columna in maximos:
            dataframe_normalizado[columna] = (dataframe[columna] - minimos[columna]) / (maximos[columna] - minimos[columna])
    return dataframe_normalizado

In [164]:
# Función principal de procesamiento
def procesar_dataframes(dataframes_dict, modelo_lstm, minimos_path, maximos_path, window_size=1, n_individuos_poblacion=5, generations=5):
    """
    Procesa múltiples DataFrames dividiéndolos en bloques, normalizándolos, aplicando un algoritmo genético a cada bloque,
    y consolidando los resultados en un DataFrame final para cada DataFrame original.

    Args:
        dataframes_dict (dict): Diccionario con los DataFrames a procesar.
        modelo_lstm: Modelo LSTM ya entrenado para el algoritmo genético.
        minimos_path (str): Ruta al archivo JSON con los valores mínimos.
        maximos_path (str): Ruta al archivo JSON con los valores máximos.
        window_size (int): Tamaño de la ventana deslizante.
        n_individuos_poblacion (int): Número de individuos en la población del algoritmo genético.
        generations (int): Número de generaciones del algoritmo genético.

    Returns:
        dict: Diccionario con los DataFrames procesados y consolidados.
    """
    # Cargar los valores mínimos y máximos
    with open(minimos_path, "r") as file:
        minimos = json.load(file)
    with open(maximos_path, "r") as file:
        maximos = json.load(file)

    # Diccionario para almacenar los resultados finales
    recomendaciones_dict = {}

    # Número de bloques a dividir
    num_bloques = 8


    # Recorrer cada DataFrame en el diccionario
    for key, df in dataframes_dict.items():
        print(f"\nProcesando el DataFrame {key}...")

        # Dividir el DataFrame en bloques
        bloques_origen = dividir_en_bloques(df, num_bloques)

        # Determinar las variables a normalizar (excluyendo las dos últimas columnas)
        variables_a_normalizar = bloques_origen['bloque_1'].columns[:-2]

        # Normalizar cada bloque
        for bloque_key, bloque_df in bloques_origen.items():
            bloques_origen[bloque_key] = normalizar_por_variables_max_min(
                bloque_df, variables_a_normalizar, minimos, maximos
            )

        # Lista para consolidar los resultados de los bloques
        df_resultados_bloques = []

        # Procesar cada bloque individualmente
        for bloque_key, bloque_df in bloques_origen.items():
            print(f"  Procesando {bloque_key} con {len(bloque_df)} filas...")

            # Crear ventanas deslizantes para el bloque
            resultados = create_sliding_windows(bloque_df, window_size)

            # Medir el tiempo de ejecución del algoritmo genético
            start_time = time.time()

            # Aplicar el algoritmo genético al bloque
            df_resultados_recomendacion = aplicar_algoritmo_genetico_por_bloques(
                modelo_lstm, resultados, window_size=1, n_individuos_poblacion=5, generations=5)
            
            end_time = time.time()

            # Agregar los resultados del bloque a la lista
            df_resultados_bloques.append(df_resultados_recomendacion)

            print(f"    {bloque_key} procesado en {end_time - start_time:.2f} segundos.")

        # Consolidar los resultados de todos los bloques para el DataFrame actual
        df_recomendacion = pd.concat(df_resultados_bloques, ignore_index=True)

        # Almacenar el resultado consolidado
        recomendaciones_dict[f"{key}_recomendacion"] = df_recomendacion

        print(f"DataFrame {key} procesado y consolidado.")

    return recomendaciones_dict

In [165]:
#Ejemplo de uso:
recomendaciones = procesar_dataframes(
    dataframes_dict,
    modelo_lstm,
    "minimos_lstm_13_var.json",
    "maximos_lstm_13_var.json",
    window_size=1,
    n_individuos_poblacion=5,
    generations=5
)


Procesando el DataFrame df_proyectocombustible_presentation/ModeloDinamico/datacamion/28/...
  Procesando bloque_1 con 56 filas...
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 168ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20m

/tmp/ipykernel_120300/2923353968.py:370: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_resultados_final = pd.concat([df_resultados_final, df_temp], ignore_index=True)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step

Mejor individuo (minimizar consumo de combustible): [[8.65473688e-01 9.81246930e-01 5.95385665e-01 8.64873451e-01
  8.24921802e-01 9.97441487e-03 9.99703934e-03 9.

/tmp/ipykernel_120300/2923353968.py:370: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_resultados_final = pd.concat([df_resultados_final, df_temp], ignore_index=True)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step

Mejor individuo (minimizar consumo de combustible): [[4.37210739e-01 9.77035598e-01 2.26229898e-02 7.57219607e-01
  3.34291634e-01 9.83243585e-03 9.99801029e-03 9.

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step

Mejor individuo (minimizar consumo de combustible): [[6.34989202e-01 9.81972710e-01 5.79799689e-01 6.44220428e-01
  1.8706913

/tmp/ipykernel_120300/2923353968.py:370: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_resultados_final = pd.concat([df_resultados_final, df_temp], ignore_index=True)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step

Mejor individuo (minimizar consumo de combustible): [[5.52607238e-01 9.78250113e-01 1.51294084e-01 6.21959847e-01
  9.46831069e-01 9.91337820e-03 9.99792220e-03 9.

/tmp/ipykernel_120300/2923353968.py:370: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_resultados_final = pd.concat([df_resultados_final, df_temp], ignore_index=True)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 27ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step

Mejor individuo (minimizar consumo de combustible): [[5.10644913e-01 9.82431674e-01 7.01399816e-01 6.74068498e-01
  9.32159784e-01 9.95732427e-03 9.99738923e-03 9.

In [177]:
recomendaciones['df_proyectocombustible_presentation/ModeloDinamico/datacamion/28/_recomendacion'].head()

roll  intake manifold pressure  intake manifold #2 pressure  \
0  0.576057                  0.980681                     0.546035   
1  0.865474                  0.981247                     0.595386   
2  0.915150                  0.977224                     0.033024   
3  0.585005                  0.977288                     0.020020   
4  0.585930                  0.977313                     0.018726   

   engine speed  actual gear         x         y         z  efhcargado  \
0      0.665481     0.989919  0.009932  0.009998  0.009764    0.118332   
1      0.864873     0.824922  0.009974  0.009997  0.009910    0.118332   
2      0.727388     0.421783  0.009983  0.009997  0.009721    0.118332   
3      0.101346     0.226433  0.009866  0.009999  0.009685    0.183323   
4      0.167872     0.275666  0.009866  0.009999  0.009684    0.183323   

   efhvacio  distancia_ruta_pendiente_grados  ambient air temperature  \
0  0.163112                         0.305268                 0.999460   
1  0.163112                         0.305268                 0.999442   
2  0.163112                         0.305268                 0.999430   
3  0.251882                         0.282634                 0.999298   
4  0.251882                         0.282634                 0.999298   

   brake pump pressure  fuel consumption rate(lag1)  \
0             0.003942                   116.787315   
1             0.005356                   199.822632   
2             0.003798                   190.594543   
3             0.003602                   242.168289   
4             0.008341                   279.017731   

   fuel consumption rate(target)  
0                     198.602081  
1                     230.926117  
2                     254.459991  
3                     210.323242  
4                     215.838974

In [123]:
# Parte 5, Desescalamos los datos 

def desescalar_por_variables_max_min(dataframe_normalizado, variables_a_desescalar, minimos, maximos):
    """
    Desescala solo las variables especificadas en un dataframe utilizando el método inverso de Min-Max.
    Args:
        dataframe_normalizado: El dataframe con valores normalizados.
        variables_a_desescalar: Lista de nombres de las variables a desescalar.
        minimos: Diccionario con el valor mínimo de cada variable.
        maximos: Diccionario con el valor máximo de cada variable.
    Returns:
        DataFrame desescalado con valores originales.
    """
    dataframe_desescalado = dataframe_normalizado.copy()
    for columna in variables_a_desescalar:
        if columna in minimos and columna in maximos:
            dataframe_desescalado[columna] = dataframe_normalizado[columna] * (maximos[columna] - minimos[columna]) + minimos[columna]
    return dataframe_desescalado

# Variables a normalizar (excluyendo la última columna)
variables_a_desescalar = df_resultados_recomendacion_b1.columns[:-2]  # Excluir el target y el lag, que no se deben escalar

# Aplicar la desescalación
df_resultados_recomendacion_b1_desescalado = desescalar_por_variables_max_min(df_resultados_recomendacion_b1, variables_a_desescalar, minimos, maximos)

In [125]:
# df_resultados_recomendacion_b1_desescalado

In [ ]:
# Parte 6, Aplicar recomendaciones finales del Algoritmo Evolutivo
def aplica_recomendaciones_finales(df_original, df_desescalado, columna_objetivo, columna_redondeo):
    """
    Aplica las recomendaciones basadas en una condición y actualiza las filas del DataFrame original con el DataFrame desescalado.
    
    Parameters:
    df_original (pd.DataFrame): DataFrame original con los datos base.
    df_desescalado (pd.DataFrame): DataFrame con los valores desescalados.
    columna_objetivo (str): Nombre de la columna objetivo para la comparación.
    columna_redondeo (str): Nombre de la columna que se debe redondear al final.

    Returns:
    pd.DataFrame: DataFrame actualizado con las recomendaciones aplicadas.
    """
    # Asegurar que los índices son idénticos
    df_original = df_original.reset_index(drop=True)
    df_desescalado = df_desescalado.reset_index(drop=True)
    
    # Crear una copia del DataFrame original para modificar
    df_final = df_original.copy()
    
    # Condición de comparación
    condicion = df_desescalado[columna_objetivo] < df_original[columna_objetivo]
    
    # Actualizar las filas donde se cumple la condición
    df_final.loc[condicion] = df_desescalado.loc[condicion]
    
    # Redondear la columna especificada
    df_final[columna_redondeo] = df_final[columna_redondeo].round()
    
    return df_final


df_finalrecomendacion_b1 = aplica_recomendaciones_finales(df_original=bloques_origen_b1,df_desescalado=df_resultados_recomendacion_b1_desescalado,
    columna_objetivo="fuel consumption rate(target)",
    columna_redondeo="actual gear"
)

In [39]:
# dataframes_dict['df_proyectocombustible_presentation/ModeloDinamico/datacamion/45/'].head()

In [31]:
# Procesar los DataFrames
resultados_finales = {}

for key, df in dataframes_dict.items():
    print(f"Procesando {key}...")
    
    # Crear ventanas deslizantes
    df_windows = create_sliding_windows(df, window_size=window_size)
    print(f"  {len(df_windows)} ventanas generadas para {key}.")
    
    # Ejecutar el algoritmo genético en cada ventana
    poblaciones_finales = []
    for j, window in enumerate(df_windows):
        print(f"  Ejecutando algoritmo genético en ventana {j+1} de {len(df_windows)} para {key}...")
        final_population = run_genetic_algorithm(modelo_lstm, window, window_size=window_size)
        poblaciones_finales.append(final_population)
    
    # Almacenar resultados finales por DataFrame
    resultados_finales[key] = poblaciones_finales

# Resumen final
print("Procesamiento completado.")

instant_date_t equipment  engine coolant temperature  \
0 2024-06-27 08:08:24      CM01                        83.0   
1 2024-06-27 08:10:24      CM01                        85.0   
2 2024-06-27 08:12:24      CM01                        81.0   
3 2024-06-27 08:14:24      CM01                        82.0   
4 2024-06-27 08:16:24      CM01                        80.0   

   left exhaust temperature  final drive oil bypass solenoid status  \
0                     515.0                                     1.0   
1                     431.0                                     0.0   
2                     181.0                                     0.0   
3                     427.0                                     0.0   
4                     181.0                                     0.0   

   right brake cooling filter status  \
0                                NaN   
1                                NaN   
2                                NaN   
3                                NaN   
4                                NaN   

   rear axle pump drive oil divert solenoid status  right rear axle rpm  \
0                                              0.0                833.0   
1                                              0.0                219.0   
2                                              0.0                741.0   
3                                              0.0                395.0   
4                                              0.0                246.0   

   fuel pressure  engine speed  brake pump unloader solenoid status  \
0          631.0        1453.5                                  1.0   
1          609.0        1315.0                                  1.0   
2          673.0        1817.5                                  1.0   
3          619.5        1285.5                                  1.0   
4          647.0        1352.0                                  1.0   

   shift lever position  steering accumulator oil pressure  \
0               16390.0                            21724.0   
1               16390.0                            21731.0   
2               16388.0                            21598.0   
3               16390.0                            21559.0   
4               16390.0                            20574.0   

   left front brake oil temperature  \
0                              83.0   
1                              83.0   
2                              91.0   
3                              86.0   
4                              90.0   

   turbocharger #3 compressor inlet pressure (absolute)  service brake  \
0                                          60.869999               0.0   
1                                          61.580002               0.0   
2                                          61.900002               0.0   
3                                          61.619999               0.0   
4                                          61.490002               0.0   

   fuel rail temperature  desired fuel rail pressure  \
0              76.589996                    120656.0   
1              75.889999                    108516.0   
2              76.589996                    132092.0   
3              78.089996                    110084.0   
4              73.500000                    113624.0   

   desired brake cooling pump speed  differential (axle) lube pressure  \
0                               0.0                              700.5   
1                               0.0                              741.5   
2                               0.0                              715.5   
3                            2004.0                              654.0   
4                               0.0                              841.0   

   diff oil temperature  altitude derate  auto lube relay status  \
0                 192.0              0.0                     0.0   
1                 192.0              0.0                     0.0   
2                 192.0              0.0   